# Google Review Preprocessing version1 

## version0에서 발견된 문제점 
1. 맞춤법이 틀린 문장은 추후 토크나이징할 때 영향있을거 같음.
2. (Google 번역)처럼 괄호로 둘러쌓인 단어들이 '번역', '원문'과 같은 단어로 남아있음.
3. 코드 정리 필요
4. 전체 데이터셋에 대한 정제 데이터셋 만들어야함.

## version1에서 발견된 문제점
1. dataframe에 keyword 다르게 매칭됨. 
2. 맞춤법 교정 후 데이터 전처리 안 해줌. 
3. 제대로 전처리가 진행됐는지 확인하는 코드 없음.

## Data path 확인

In [5]:
!pwd # 현재 경로 확인 

/home/aiffel-dj19/jungcheck/DataPreprocessing


아래 tree 명령어로 상위 폴더(jungcheck)내 파일 구성을 볼 수 있습니다.    

In [6]:
!ls . # 현재 위치의 file list

data				   googleReviewPreprocessingV1.ipynb  reference
filtered			   naverReviewPreprocessingV0.ipynb
googleReviewPreprocessingV0.ipynb  naverReviewPreprocessingV1.ipynb


In [7]:
!tree -L 3 -N ./data/google_review # jungcheck 폴더내 경로 확인 

./data/google_review
├── 01오월드
│   └── 오월드.csv
├── 02뿌리공원
│   └── 뿌리공원.csv
├── 03엑스포
│   ├── 한빛탑.csv
│   ├── 엑스포다리.csv
│   ├── 엑스포음악분수.csv
│   ├── 엑스포과학공원.csv
│   └── 세계엑스포기념품박물관.csv
├── 04한밭수목원
│   └── 한밭수목원.csv
├── 05계족산
│   ├── 계족산(봉우리읍내동).csv
│   ├── 계족산성.csv
│   └── 계족산황톳길.csv
├── 06대청호
│   ├── 대청호.csv
│   ├── 대청댐물문화관.csv
│   └── 대청호반자연생태공원.csv
├── 07장태산
│   ├── 장태산자연휴양림.csv
│   ├── 장태산자연휴양림전망대.csv
│   ├── 장태산자연휴양림숲속의집.csv
│   └── 장태산자연휴양림메타세콰이어산림욕장.csv
├── 09동춘당
│   ├── 회덕동춘당.csv
│   └── 동춘당공원.csv
├── 11으능정이문화의거리
│   ├── 으능정이거리.csv
│   ├── 대전스카이로드.csv
│   └── 으능정이문화거리.csv
├── 12유성온천
│   ├── 유성온천공원.csv
│   └── 유성온천족욕체험장.csv
├── 13성심당
│   ├── 성심당본점.csv
│   ├── 성심당대전역점.csv
│   ├── 성심당케잌부띠끄본점.csv
│   ├── 성심당롯데백화점대전점.csv
│   └── 성심당DCC점.csv
├── 13시민천문대
│   └── 대전시민천문대.csv
├── 14수통골
│   ├── 수통골유원지.csv
│   └── 계룡산국립공원수통골지구.csv
├── 16대전문화예술단지
│   ├── 이응노미술관.csv
│   ├── 대전예술의전당.csv
│   └── 대전시립미술관.csv
└── 17국립중앙과학관
    └── 국립중앙과학관.csv

15 directories, 37 files


## Library Import

In [8]:
import os 
import glob
from tqdm import tqdm

import re
import pandas as pd 
import copy # deep copy

from hanspell import spell_checker # 한글 맞춤법 검사기 
from hangul_checker import KoreanSpellChecker # 한글 맞춤법 검사기 
from pykospacing import Spacing # 한글 띄어쓰기 검사기 

## Data Load 

In [9]:
data_path = os.path.join(os.getcwd(), 'data/google_review/')
data_path

'/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/'

In [10]:
folders = os.listdir(data_path)
print(folders)
print(len(folders)) # 17개 대상 관광지 중 15개 

['07장태산', '05계족산', '09동춘당', '11으능정이문화의거리', '02뿌리공원', '03엑스포', '13성심당', '14수통골', '12유성온천', '04한밭수목원', '17국립중앙과학관', '06대청호', '16대전문화예술단지', '13시민천문대', '01오월드']
15


👉 17개 대상 관광지 중에 15개 데이터만 크롤링 해올 수 있었습니다. 구글 리뷰 같은 경우 한밭야구장과 둘레길은 리뷰가 없거나 2개 이하 였기 때문에 데이터셋에 포함되지 않습니다.    
👉 감성 분석 결과를 네이버 블로그 리뷰와 합쳐서 17개 대상 관광지들에 대한 감성 분석을 진행합니다.
👉 카이스트 같은 경우 크롤링 데이터셋에 있었지만, 대상 관광지에 포함되지 않아 코드 진행하기 전에 디렉토리에서 삭제했습니다.

In [11]:
# 대전관광 홈페이지 영문버전을 참고했으며(단, 긴 경우 줄임), 해당 리스트는 정제후 파일명으로 사용
# 나오지 않는 관광지는 네이버 검색 기준을 따름
keywords_ko = [file_name[2:] for file_name in folders]
keywords_en = ['jangtae_mountain', 'gyejok_mountain', 'dongchundang', 'uineungjeongi_street', 'ppuri_park', 
               'expo_science_park', 'sungsimdang_bakery', 'water_barrel', 'yuseong_hotspring', 'hanbat_arboretum', 
               'science_museum','daecheong_lake', 'art_culture_complex', 'observatory', 'oworld_zoo']

keywords = {k:v for k, v in zip(keywords_ko, keywords_en)}
keywords

{'장태산': 'jangtae_mountain',
 '계족산': 'gyejok_mountain',
 '동춘당': 'dongchundang',
 '으능정이문화의거리': 'uineungjeongi_street',
 '뿌리공원': 'ppuri_park',
 '엑스포': 'expo_science_park',
 '성심당': 'sungsimdang_bakery',
 '수통골': 'water_barrel',
 '유성온천': 'yuseong_hotspring',
 '한밭수목원': 'hanbat_arboretum',
 '국립중앙과학관': 'science_museum',
 '대청호': 'daecheong_lake',
 '대전문화예술단지': 'art_culture_complex',
 '시민천문대': 'observatory',
 '오월드': 'oworld_zoo'}

👉 대전관광 홈페이지 영문버전을 참고했습니다. (단, 긴 경우 줄임)    
👉 맨 뒤에 단어는 해당 관광지가 어떤 유형의 장소에 해당하는지를 나타내는 단어로 통일성을 줬습니다. 감성 분석을 할 때 성능이 잘 안 나오다면, 장소 유형이 같은 대상끼리 단어사전을 만들어주는 방법도 생각해볼 수 있습니다. 

In [16]:
if '장태산' in keywords.keys():
    print(keywords['장태산'])

jangtae_mountain


In [17]:
# root_path내의 dataframe을 합해주는 함수
def concatCsv(root_path:str, keys:dict, folders_list:list):
    data_list = []
    
    for folder in folders_list:
        folder_path = os.path.join(root_path, folder)
        key_ko = folder[2:]
        
        for file in os.listdir(folder_path):
            file_path = os.path.join(folder_path, file)
            print(file_path)
            
            search = file.split('.')[0]               # 파일명에서 키워드만 추출    
            df = pd.read_csv(file_path, encoding='utf-8')  # csv 파일 읽기
            df['search'] = search
            
            if key_ko in keywords.keys():
                df['keyword'] = keywords[key_ko]
            data_list.append(df)
        print('-'*20)
    df = pd.concat(data_list, axis=0)

    return df

In [18]:
data_df = concatCsv(data_path, keywords, folders)

/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림메타세콰이어산림욕장.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림전망대.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림숲속의집.csv
--------------------
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/05계족산/계족산황톳길.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/05계족산/계족산(봉우리읍내동).csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/05계족산/계족산성.csv
--------------------
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/09동춘당/회덕동춘당.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/09동춘당/동춘당공원.csv
--------------------
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/11으능정이문화의거리/으능정이거리.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/11으능정이문화의거리/대전스카이로드.

In [19]:
data_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
4             JY Jeong         4  8달 전   
..                  ...      ...   ...   
925                김경영         4  1년 전   
926               패티가고         5  1년 전   
927                이종진         3  1년 전   
928                김소연         5  1년 전   
929            별사탕이랑햄찌         3  1년 전   

                                               comment              search  \
0                    여기는 갈 때마다 새로운 느낌이야 즐거운 시간이 되었습니다.  장태산자연휴양림메타세콰이어산림욕장   
1                                하늘보고 누워 힐링하기 넘 좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘 정리된 메타세쿼이아 숲에서 산림욕 하기 좋은 곳으로 둘레길 걷기와 전망대까지 가...  장태산자연휴양림메타세콰이어산림욕장   
3                                       산책 하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장   
4                                                   없음  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
925                                               괜찮아요                 오월드   
926                                                 없음                 오월드   
927                                                 없음                 오월드   
928                                     겨울에도 놀기 좋아요~ㅎㅎ                 오월드   
929                                                 없음                 오월드   

              keyword  
0    jangtae_mountain  
1    jangtae_mountain  
2    jangtae_mountain  
3    jangtae_mountain  
4    jangtae_mountain  
..                ...  
925        oworld_zoo  
926        oworld_zoo  
927        oworld_zoo  
928        oworld_zoo  
929        oworld_zoo  

[18800 rows x 6 columns]

In [20]:
type(data_df['keyword'].iloc[0])

str

In [21]:
# keyword 누락된 열 없는지 확인
data_df['keyword'].isnull().sum()

0

In [23]:
# keyword 구성 동일한지 확인 
sorted(keywords.values()) == sorted(list(set(data_df['keyword'])))

True

## Data cleaning
* null 처리 
* 일정 길이 이하의 문자열 제거 
* 중복 제거 

In [24]:
# null 처리
print(f'Before length: {len(data_df)}')

data_df = data_df[data_df['comment'] != '없음']
print(f'After length: {len(data_df)}')

Before length: 18800
After length: 8635


In [25]:
# 단어 1개인 경우 확인 
data_df[data_df['comment'].map(len) == 1]

name  ratings   date comment        search  \
63             채규삼         5   3주 전       ㆍ      장태산자연휴양림   
521           남홍계용         5   7달 전       😀      장태산자연휴양림   
732    hunyong lee         5   9달 전       츠      장태산자연휴양림   
929            전영옥         4   1년 전       ᆞ      장태산자연휴양림   
20    남LeeSoonChul         4   3달 전       😀          계족산성   
84             허현강         5   9달 전       굿          계족산성   
526            김상민         5   2년 전       굿          계족산성   
72             물방울         5   2달 전       굳       대전스카이로드   
270         대전아트카튠         5   8달 전       굿       대전스카이로드   
278            양성혁         4   9달 전       큼       대전스카이로드   
489            문주현         3   1년 전       굿       대전스카이로드   
869            조원화         5   1년 전       굿       대전스카이로드   
17             항아리         5   2주 전       굳          뿌리공원   
114           99마루         5   2달 전       굳          뿌리공원   
283            최일훈         5   6달 전       😃          뿌리공원   
324            박수민         5   6달 전       ㅁ          뿌리공원   
504            이영화         5  11달 전       네          뿌리공원   
5              전유진         5   2일 전       굿         엑스포다리   
190            김준선         5   6달 전       굿         엑스포다리   
8              노태훈         4   2일 전       굿           한빛탑   
58            잘난서방         4   2주 전       굿       성심당DCC점   
365            최일훈         5   4달 전       굿       성심당DCC점   
513     Jihong Min         5   6달 전       💜       성심당DCC점   
543             오현         5   6달 전       빵       성심당DCC점   
15    Jong Suk Woo         4   2일 전       ㅇ         성심당본점   
79             김한별         5   2주 전       굿         성심당본점   
493            정원오         5   3달 전       ㅇ         성심당본점   
576          냥아치TV         5   3달 전       굳         성심당본점   
726            오세훈         5   5달 전       굿         성심당본점   
16             한석화         5   2주 전       굿   성심당롯데백화점대전점   
433            노희찬         4  10달 전       굳   성심당롯데백화점대전점   
502             자옹         3   8달 전       굳  계룡산국립공원수통골지구   
14             장윤주         5   1달 전       굿     유성온천족욕체험장   
100            이종민         5   1달 전       굿         한밭수목원   
210     jongku LEE         5   2달 전       굿         한밭수목원   
554           한 상영         5   8달 전       ㅕ         한밭수목원   
384            황혜미         5   1년 전       굿       국립중앙과학관   
11             지성구         4   2주 전       굿       대전예술의전당   
290            신지완         5   1년 전       굳       대전예술의전당   
314            정종길         5   1년 전       굿       대전예술의전당   
320           스텔라김         5   1년 전       짱       대전예술의전당   
110            쭉쟁이         5   1년 전       굿       대전시립미술관   
47             강적봉         5   8년 전       짱       대전시민천문대   
68            잘난서방         4   2주 전       굿           오월드   
101            배근효         5   3주 전       굿           오월드   
178            이예빈         5   1달 전       👌           오월드   
308            신은미         4   3달 전       뿡           오월드   
403            오진우         5   5달 전       잼           오월드   
428            류라히         5   6달 전       굿           오월드   
633    daniel. ggl         4   8달 전       굿           오월드   

                  keyword  
63       jangtae_mountain  
521      jangtae_mountain  
732      jangtae_mountain  
929      jangtae_mountain  
20        gyejok_mountain  
84        gyejok_mountain  
526       gyejok_mountain  
72   uineungjeongi_street  
270  uineungjeongi_street  
278  uineungjeongi_street  
489  uineungjeongi_street  
869  uineungjeongi_street  
17             ppuri_park  
114            ppuri_park  
283            ppuri_park  
324            ppuri_park  
504            ppuri_park  
5       expo_science_park  
190     expo_science_park  
8       expo_science_park  
58     sungsimdang_bakery  
365    sungsimdang_bakery  
513    sungsimdang_bakery  
543    sungsimdang_bakery  
15     sungsimdang_bakery  
79     sungsimdang_bakery  
493    sungsimdang_bakery  
576    sungsimdang_bakery  
726    sungsimdang_bakery  
16     sungsimdang_bakery  
433    sungsimdang_bakery  
502    

데이터를 확인했을때 유의미한 경우에 모두 해당했기 때문에 length=1인 데이터 유지 

In [26]:
# 단어 0개인 comment 제외 
print(f'Before length: {len(data_df)}')

data_df = data_df[data_df['comment'].map(len) > 0] 
print(f'After length: {len(data_df)}')

Before length: 8635
After length: 8635


In [27]:
# 중복제거 
print(f'Before length: {len(data_df)}')

data_df = data_df.drop_duplicates(['name', 'keyword', 'date']) # name과 keyword, date 모두 중복일때 제거 
print(f'After length: {len(data_df)}')

Before length: 8635
After length: 8466


In [28]:
data_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                    여기는 갈 때마다 새로운 느낌이야 즐거운 시간이 되었습니다.  장태산자연휴양림메타세콰이어산림욕장   
1                                하늘보고 누워 힐링하기 넘 좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘 정리된 메타세쿼이아 숲에서 산림욕 하기 좋은 곳으로 둘레길 걷기와 전망대까지 가...  장태산자연휴양림메타세콰이어산림욕장   
3                                       산책 하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장   
6                          주말마자 애정하는 장태산나들이:-) 단풍도 예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                           재밌어요..😍😍                 오월드   
922                                       애들놀고 구경거리는 굿                 오월드   
924                             초등생전용놀이공원으로  아담하고  이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                     겨울에도 놀기 좋아요~ㅎㅎ                 오월드   

              keyword  
0    jangtae_mountain  
1    jangtae_mountain  
2    jangtae_mountain  
3    jangtae_mountain  
6    jangtae_mountain  
..                ...  
921        oworld_zoo  
922        oworld_zoo  
924        oworld_zoo  
925        oworld_zoo  
928        oworld_zoo  

[8466 rows x 6 columns]

## Data preprocessing

In [60]:
filtered_df = copy.deepcopy(data_df)

데이터셋을 살펴보면, 외국인이 작성한 것도 한글로 번역되어 크롤링됐다.
따로 영어를 살려줄 필요 없어 보이므로 한글, ~숫자~ 제외하고 다 제거한다. 

In [61]:
# 번역, 원문과 같이 구글 번역에 의해 나타나는 단어를 제거하는 정규표현식 패턴
test = '안녕하 (번역 제공) 번역 원문 안녕하'
test = re.sub("[번역 제공|번역|원문]", "", test)
test = re.sub("[(].*?[)]", "", test)
test

'안녕하안녕하'

In [62]:
# filtered_df['comment'] = filtered_df['comment'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")
filtered_df['comment'] = filtered_df['comment'].str.replace("[(].*?[)]","", regex=True) # 괄호 사이 단어 제거
filtered_df['comment'] = filtered_df['comment'].str.replace("[번역 제공|번역|원문]","", regex=True) # 위에 정규표현식 적용안되서 다시 적용
filtered_df['comment'] = filtered_df['comment'].str.replace("[^가-힣]","", regex=True) # 완성형 한글만
filtered_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                            여기는갈때마다새로운느낌이야즐거운시간이되었습니다  장태산자연휴양림메타세콰이어산림욕장   
1                                    하늘보고누워힐링하기넘좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘정리된메타세쿼이아숲에서산림욕하기좋은곳으로둘레길걷기와전망대까지가벼운등산활동까지할수있...  장태산자연휴양림메타세콰이어산림욕장   
3                                           산책하기너무좋은명소  장태산자연휴양림메타세콰이어산림욕장   
6                                 주말마자애정하는장태산나들이단풍도예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                               재밌어요                 오월드   
922                                         애들놀고구경거리는굿                 오월드   
924                                   초등생전용놀이으로아담하고이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                          겨울에도놀기좋아요                 오월드   

              keyword  
0    jangtae_mountain  
1    jangtae_mountain  
2    jangtae_mountain  
3    jangtae_mountain  
6    jangtae_mountain  
..                ...  
921        oworld_zoo  
922        oworld_zoo  
924        oworld_zoo  
925        oworld_zoo  
928        oworld_zoo  

[8466 rows x 6 columns]

👉 정규표현식을 통해 제거 후에, 문장 구성이 달라지기 때문에 cleaning 작업을 위와 똑같이 다시 진행해줍니다.

In [63]:
# 단어 1개인 경우 확인 
filtered_df[filtered_df['comment'].map(len) == 1]

name  ratings   date comment    search           keyword
695   Soo Young Yoo         5   8달 전       굿  장태산자연휴양림  jangtae_mountain
732     hunyong lee         5   9달 전       츠  장태산자연휴양림  jangtae_mountain
84              허현강         5   9달 전       굿      계족산성   gyejok_mountain
324   Soo Young Yoo         5   1년 전       굿      계족산성   gyejok_mountain
526             김상민         5   2년 전       굿      계족산성   gyejok_mountain
..               ...      ...    ...     ...       ...               ...
403             오진우         5   5달 전       잼       오월드        oworld_zoo
428             류라히         5   6달 전       굿       오월드        oworld_zoo
633     daniel. ggl         4   8달 전       굿       오월드        oworld_zoo
693             손장현         5  10달 전       굿       오월드        oworld_zoo
876          jian k         5   1년 전       음       오월드        oworld_zoo

[63 rows x 6 columns]

👉 데이터를 확인했을때 유의미한 경우에 모두 해당했기 때문에 length=1인 데이터 유지했습니다. 

In [64]:
# 단어 0개인 comment 제외 
print(f'Before length: {len(filtered_df)}')

filtered_df = filtered_df[filtered_df['comment'].map(len) > 0] 
print(f'After length: {len(filtered_df)}')

Before length: 8466
After length: 8427


In [65]:
# 중복제거 
print(f'Before length: {len(filtered_df)}')

filtered_df = filtered_df.drop_duplicates(['name', 'keyword', 'date']) # name과 keyword, date 모두 중복일때 제거 
print(f'After length: {len(filtered_df)}')

Before length: 8427
After length: 8427


In [66]:
filtered_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                            여기는갈때마다새로운느낌이야즐거운시간이되었습니다  장태산자연휴양림메타세콰이어산림욕장   
1                                    하늘보고누워힐링하기넘좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘정리된메타세쿼이아숲에서산림욕하기좋은곳으로둘레길걷기와전망대까지가벼운등산활동까지할수있...  장태산자연휴양림메타세콰이어산림욕장   
3                                           산책하기너무좋은명소  장태산자연휴양림메타세콰이어산림욕장   
6                                 주말마자애정하는장태산나들이단풍도예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                               재밌어요                 오월드   
922                                         애들놀고구경거리는굿                 오월드   
924                                   초등생전용놀이으로아담하고이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                          겨울에도놀기좋아요                 오월드   

              keyword  
0    jangtae_mountain  
1    jangtae_mountain  
2    jangtae_mountain  
3    jangtae_mountain  
6    jangtae_mountain  
..                ...  
921        oworld_zoo  
922        oworld_zoo  
924        oworld_zoo  
925        oworld_zoo  
928        oworld_zoo  

[8427 rows x 6 columns]

## 맞춤법 교정

In [67]:
def spacingCorrect(sen):
    spacing = Spacing(rules=keywords_ko+['이뻐요'])
#     print(f'Before sentence: {sen}')

    sen = spacing(sen)
#     print(f'After sentence: {sen}')
#     print('-'*40)
    
    return sen

In [68]:
def spellCorrect(sen):
#     ksc = KoreanSpellChecker()
#     print(f'Before sentence: {sen}')

#     sen = ksc.check_spelling(sen)
#     print(f'After sentence: {sen}')
#     print('-'*40)
    result = spell_checker.check(sen)
    sen = result.as_dict()['checked']
    return sen

In [69]:
print(f'Before length: {len(filtered_df)}')

Before length: 8427


In [70]:
# 4분 34초 소요
filtered_df['comment'] = [spacingCorrect(sen) for sen in tqdm(filtered_df['comment'])]

100%|██████████| 8427/8427 [04:28<00:00, 31.38it/s]


In [71]:
print(f'After length: {len(filtered_df)}')

After length: 8427


In [73]:
print(f'Before length: {len(filtered_df)}')

Before length: 8427


In [72]:
# KoreanSpellChecker
# filtered_df = filtered_df[filtered_df['comment'].map(len) <= 500] # name과 keyword, date 모두 중복일때 제거 

👉 KoreanSpellChecker를 사용할 경우, 맞춤법 검사기의 최대 허용 글자수는 500자이므로, 글자수 제한을 둬야합니다.

In [74]:
# Hanspell - 7분 4초 정도 소요
filtered_df['comment'] = [spellCorrect(sen) for sen in tqdm(filtered_df['comment'])]

100%|██████████| 8427/8427 [06:42<00:00, 20.92it/s]


In [75]:
print(f'After length: {len(filtered_df)}')

After length: 8427


In [76]:
# set pandas option 
pd.set_option('display.max_rows', None) # 전체 행 보기
pd.set_option('display.max_columns', None) # 전체 열 보기 
pd.set_option('display.expand_frame_repr', False)

In [77]:
# 단어 0개인 comment 제외 
print(f'Before length: {len(filtered_df)}')

filtered_df = filtered_df[filtered_df['comment'].map(len) > 0] 
print(f'After length: {len(filtered_df)}')

Before length: 8427
After length: 8426


In [78]:
# 중복제거 
print(f'Before length: {len(filtered_df)}')

filtered_df = filtered_df.drop_duplicates(['name', 'keyword', 'date']) # name과 keyword, date 모두 중복일때 제거 
print(f'After length: {len(filtered_df)}')

Before length: 8426
After length: 8426


In [79]:
# 단어 1개인 경우 comment값 확인 
one_length = filtered_df[filtered_df['comment'].map(len) == 1]['comment']
one_length = list(set(one_length))
one_length

['굳', '굿', '음', '네', '큰', '용', '잼', '쉬', '뿡', '앙', '츠', '빵', '짱', '큼']

👉 한 글자로 된 단어 중에서는 '잼', '짱', '굳', '굿', '큼', '큰' 외에는 리뷰로 볼 수 없어 그 외는 삭제합니다. 

In [80]:
def oneLength(row: str):
    one_length = ['잼', '짱', '굳', '굿', '큼', '큰'] 

    if len(row)==1 and row in one_length: return row
    elif len(row)==1 and row not in one_length: return ""
    else: return row

In [81]:
filtered_df['comment'] = filtered_df['comment'].apply(oneLength)
filtered_df

name  ratings    date                                            comment              search               keyword
0                                             미샤         4    2주 전                  여기는 갈 때마다 새로운 느낌이 야 즐거운 시간이 되었습니다  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
1                               Gyang gree young         5    3주 전                           하늘 보고 누워 힐링하기 너무 좋은 곳이에요  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
2                                            박진수         5    3달 전  잘 정리된 메타세쿼이아 숲에서 산림욕하기 좋은 곳으로 둘레길 걷기와 전망대까지 가벼...  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
3                                        Sh Choi         5    7달 전                                      산책하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
6                                            박은선         5    1년 전                        주말 마자 애정 하는 장태산 나들이 단풍도 예뻐요  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
7                                             아빠         5    1년 전                         무료인데다가 쉴 곳이 많고 시설이 잘 되어 있다  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
8                                         LEE가이버         5    1년 전  관람료 무료여서 좋고요 전망대까지 분 정도 걸리는 완만한 산책길은 대화하면서 올라가...  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
9                                            이해일         5    1년 전                                        대전의 좋은 산림욕장  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
10                                           이승주         5    1년 전                                       힐링 되고 아주 좋네요  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
14                                           소병철         4    1년 전                                              힐링 코스  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
17                                           정기성         5    1년 전                                       주위기가 너무 새로워요  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
19                                      Hs jeong         5    1년 전  메타세콰이 아이숲이 울창하고 좋네요 산책하기에도 좋고 담에는 맛있는 음식 가져와 돗...  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
22                                         보라빛냄새         5    1년 전                                                좋아요  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
23                                           김기범         5    1년 전                                                좋아요  장태산자연휴양림메타세콰이어산림욕장      jangtae_mountain
1                                       Master K         5   9시간 전  장태산은 메타세쿼이아 나무가 높이높이 솟아 있어서 장관입니다 전망대나 흔들 다리도 ...            장태산자연휴양림      jangtae_mountain
3                                           대전용달         5    2일 전                                              기 좋아요            장태산자연휴양림      jangtae_mountain
4                                   Youngki Hong         5    2일 전                                                좋아요            장태산자연휴양림      jangtae_mountain
7                                            정성식         5    4일 전       메타 크로스 나무가 너무 멋있고 기 좋고 푸르름에 건강해지는 느낌 진짜 좋았어요            장태산자연휴양림      jangtae_mountain
9                                            정재곤         4    5일 전                                   다시 한가 보고 싶은 곳입니다            장태산자연휴양림      jangtae_mountain
14                                           박은희         5    1주 전                                             정말 좋아요            장태산자연휴양림      jangtae_mountain
19                                           장래소         3    1주 전           저 주일에 오랜만에 텐트를 펼치고 잠시나마 아이들과 휴식을 하고 왔습니다            장태산자연휴양림      jangtae_mountain
23                                           이종후         5    1주 전                                   가볍게 산책하기 좋은 곳입니다            장태산자연휴양림      jangtae_mountain
28                                    Kim Jinwoo         5    1주 전  쥐라기부터 단일 품종으로 생존하고 있는 메타세쿼이아 숲이 주연하는 초록의 향연을 맛...            장태산자연휴양림      jangtae_mountain
31                                           황영주         5    2주 전                                             시힐링 최고            장태산자연휴양림      jangtae_mountain
32                                        소크더

In [82]:
# 단어 0개인 comment 제외 
print(f'Before length: {len(filtered_df)}')

filtered_df = filtered_df[filtered_df['comment'].map(len) > 0] 
print(f'After length: {len(filtered_df)}')

Before length: 8426
After length: 8417


In [83]:
# 전체 keywords가 다 포함됐는지 확인
sorted(keywords.values()) == sorted(list(set(filtered_df['keyword'])))

True

445

In [104]:
for _, key_en in keywords.items():
    cnt = filtered_df[filtered_df['keyword']==key_en]['search'].count()
    print(f'{key_en}과 연관된 검색어는 {cnt}개')
    print(list(set(filtered_df[filtered_df['keyword']==key_en]['search'])))
    print('-'*40)

jangtae_mountain과 연관된 검색어는 518개
['장태산자연휴양림전망대', '장태산자연휴양림숲속의집', '장태산자연휴양림메타세콰이어산림욕장', '장태산자연휴양림']
----------------------------------------
gyejok_mountain과 연관된 검색어는 483개
['계족산(봉우리읍내동)', '계족산황톳길', '계족산성']
----------------------------------------
dongchundang과 연관된 검색어는 328개
['동춘당공원', '회덕동춘당']
----------------------------------------
uineungjeongi_street과 연관된 검색어는 333개
['으능정이문화거리', '으능정이거리', '대전스카이로드']
----------------------------------------
ppuri_park과 연관된 검색어는 426개
['뿌리공원']
----------------------------------------
expo_science_park과 연관된 검색어는 782개
['세계엑스포기념품박물관', '엑스포과학공원', '한빛탑', '엑스포다리', '엑스포음악분수']
----------------------------------------
sungsimdang_bakery과 연관된 검색어는 1862개
['성심당대전역점', '성심당롯데백화점대전점', '성심당케잌부띠끄본점', '성심당DCC점', '성심당본점']
----------------------------------------
water_barrel과 연관된 검색어는 685개
['수통골유원지', '계룡산국립공원수통골지구']
----------------------------------------
yuseong_hotspring과 연관된 검색어는 432개
['유성온천족욕체험장', '유성온천공원']
----------------------------------------
hanbat_arboretum과 연관된

👉 검색어에 해당하는 search 컬럼을 확인하여 keyword와 매칭이 잘 됐는지 확인했습니다. 확인한 결과, keyword와 search가 잘 매칭되었음을 확인할 수 있었습니다. 

## Save csv

In [85]:
filtered_path = os.path.join(os.getcwd(), 'filtered/google_review/')
filtered_path

'/home/aiffel-dj19/jungcheck/DataPreprocessing/filtered/google_review/'

In [86]:
keywords

{'장태산': 'jangtae_mountain',
 '계족산': 'gyejok_mountain',
 '동춘당': 'dongchundang',
 '으능정이문화의거리': 'uineungjeongi_street',
 '뿌리공원': 'ppuri_park',
 '엑스포': 'expo_science_park',
 '성심당': 'sungsimdang_bakery',
 '수통골': 'water_barrel',
 '유성온천': 'yuseong_hotspring',
 '한밭수목원': 'hanbat_arboretum',
 '국립중앙과학관': 'science_museum',
 '대청호': 'daecheong_lake',
 '대전문화예술단지': 'art_culture_complex',
 '시민천문대': 'observatory',
 '오월드': 'oworld_zoo'}

In [89]:
# keyword별로 dataframe 저장 
def saveCsv(root_path: str, keys: dict, df):
    for _, key_en in keys.items():
        result_df = df[df['keyword']==key_en] 
        save_path = root_path + f'{key_en}.csv'
        result_df.to_csv(save_path, header=True, index=False)

In [92]:
saveCsv(filtered_path, keywords, filtered_df)

In [93]:
ls ./filtered/google_review/ # 파일 저장 경로내 파일 리스트 확인

art_culture_complex.csv  hanbat_arboretum.csv  science_museum.csv
daecheong_lake.csv       jangtae_mountain.csv  sungsimdang_bakery.csv
dongchundang.csv         observatory.csv       uineungjeongi_street.csv
expo_science_park.csv    oworld_zoo.csv        water_barrel.csv
gyejok_mountain.csv      ppuri_park.csv        yuseong_hotspring.csv


In [95]:
# 저장한 csv 재확인
pd.read_csv(filtered_path + 'yuseong_hotspring.csv')

name  ratings    date                                            comment     search            keyword
0                            김명숙         5    2일 전                      코로나로 한산한 유성의 이팝의 거리가 한산함에서 운함     유성온천공원  yuseong_hotspring
1                            양승일         4    1주 전                                   꽃이 약간 시든 게 아쉬워서요     유성온천공원  yuseong_hotspring
2                            민pd         5    1주 전                                            야경이 좋아요     유성온천공원  yuseong_hotspring
3                            최진식         5    2주 전                     소 연장 족욕 체험장도 있고 데이트 장소로 너무 좋아요     유성온천공원  yuseong_hotspring
4                            황영주         5    1달 전        유성구에서 수시로 관리하셔서 깨끗한 환경의 꽃길 힐링할 수 있는 곳 추천합니다     유성온천공원  yuseong_hotspring
5                         타이콩._.         5    1달 전                                       커피 한 잔 들고 산책     유성온천공원  yuseong_hotspring
6                             쮸잉         3    4달 전                                   볼 게 없던데 밤에 와야 하나     유성온천공원  yuseong_hotspring
7                  SEONGJIN MOON         5    4달 전                      최고라는 말밖에 할 말이 없다는 말밖에 할 말이 없다     유성온천공원  yuseong_hotspring
8                     Jinsuk Kim         5    5달 전                           야외 족욕 장히 있어서 많은 분들이 찾는 곳     유성온천공원  yuseong_hotspring
9                            조인선         4    7달 전                                  잘 가꾸어 놓아 보기가 좋습니다     유성온천공원  yuseong_hotspring
10                           조원진         4    7달 전                                              국화축혼잡     유성온천공원  yuseong_hotspring
11                           임춘섭         5    7달 전                                 친절하고 서비스가 좋으니까 파이팅     유성온천공원  yuseong_hotspring
12                           한영식         5    7달 전                                     코로나로 전년 대비 아쉬움     유성온천공원  yuseong_hotspring
13                           라천호         4    7달 전                                       온천수가 나와서 좋네요     유성온천공원  yuseong_hotspring
14                          깜김영찬         3    8달 전  옛날을 상상하며 왔는데 온 천지 구라기보다는 그냥 도시라고 보면 될 듯하네요 다음에...     유성온천공원  yuseong_hotspring
15                    pedro park         5   11달 전                                                 좋음     유성온천공원  yuseong_hotspring
16                           천용주         4    1년 전                                            산책하기 좋음     유성온천공원  yuseong_hotspring
17                           한병찬         5    1년 전                                       월국화축가 아름다운 곳     유성온천공원  yuseong_hotspring
18                       Ginny C         5    1년 전                                     에서 무료 따뜻한 봄 경험     유성온천공원  yuseong_hotspring
19                     G.C Cheon         3    1년 전  간단하게 발족 욕을 할 수 있는 족욕 쟁입니다 일부러 들릴만한 곳은 아니지만 쉬어가...     유성온천공원  yuseong_hotspring
20                     PE건강더하기센터         5    2년 전                              운동 삼아 걷기 좋아요 볼거리도 있고요     유성온천공원  yuseong_hotspring
21                            柳松         4    2년 전                         작은 음악 이벤트도 있고 평화 곳 있습니다 마라     유성온천공원  yuseong_hotspring
22                           곽레나         5    3년 전               위치 좋고 요족 욕탕 무료 이용 참 좋아요 일본 유후인 안 부러움     유성온천공원  yuseong_hotspring
23                     hoony kim         4    3년 전                                     어르신들이 많이 쉬시는 곳     유성온천공원  yuseong_hotspring
24                 Diomar Corpuz         5    4년 전                                                  큰     유성온천공원  yuseong_hotspring
25                      이승현.믿음으로         4  10시간 전                                   어르신분들이 너무 좋아하시네요  유성온천족욕체험장  yuseong_hotspring
26                           송재영         4    2일 전                                  도심에서 족욕을 체험할 수 있음  유성온천족욕체험장  yuseong_hotspring
27                   쩐메이커 (쩐메이커)         5    1주 전                                           아 살살 녹는다  유성온천족욕체험장  yuseong_hotspring
28                          냥이찡.         5    2주 전                                     피로도 풀리고 아주 좋아요  유성온천족욕체험장  yuseong_hotspring
29                    seongi cho         5    2주 전                   

[효율적인 dataframe 사용](https://aldente0630.github.io/data-science/2018/08/05/a-beginners-guide-to-optimizing-pandas-code-for-speed.html)

In [105]:
# dataframe list comprehension과 apply 속도 비교 => 더 느렸음..?!

In [106]:
# test_df = copy.deepcopy(data_df)

In [107]:
# test_df['comment'] = test_df['comment'].apply(lambda row: spacingCorrect(row))

In [108]:
# test_df['comment'] = test_df['comment'].apply(lambda row: spellCorrect(row))